In [21]:
from datasets import load_dataset
import pandas as pd

In [22]:
dataset = load_dataset("MickyMike/cvefixes_bigvul")

In [23]:
train_df = pd.DataFrame(list(dataset['train']))
test_df = pd.DataFrame(list(dataset['test']))

In [24]:
train_df.head()

Unnamed: 0   cwe_id                                             source  \
0           0  CWE-000  CWE-000 static void unix_release_sock ( struct...   
1           1  CWE-200  CWE-200 static void snd_timer_user_tinterrupt ...   
2           2  CWE-119  CWE-119 static void store_coding_context ( MAC...   
3           3  CWE-000  CWE-000 static int ext4_write_begin ( struct f...   
4           4  CWE-119  CWE-119 <S2SV_StartBug> int16_t vp9_ac_quant (...   

                                              target  \
0  <S2SV_ModStart> ) ; } unix_dgram_peer_wake_dis...   
1  <S2SV_ModStart> resolution ) { memset ( & r1 ,...   
2  <S2SV_ModStart> int mode_index , <S2SV_ModEnd>...   
3  <S2SV_ModStart> = page ; if ( ext4_should_dior...   
4  <S2SV_ModStart> , int delta , vpx_bit_depth_t ...   

                               project_and_commit_id         cve_id  \
0  torvalds@linux/7d267278a9ece963d77eefec6163022...  CVE-2013-7446   
1  torvalds@linux/e4ec8cc8039a7063e24204299b462bd...  CVE-2016-4578   
2  external@libvpx/5a9753fca56f0eeb9f61e342b2fccf...  CVE-2016-1621   
3  torvalds@linux/744692dc059845b2a3022119871846e...  CVE-2015-8324   
4  external@libvpx/5a9753fca56f0eeb9f61e342b2fccf...  CVE-2016-1621   

                                    original_address               time  
0  https://github.com/torvalds/linux/commit/7d267...  2015-12-28T11:59Z  
1  https://github.com/torvalds/linux/commit/e4ec8...  2016-05-23T10:59Z  
2  https://android.googlesource.com/platform/exte...  2016-03-12T21:59Z  
3  https://github.com/torvalds/linux/commit/74469...  2016-05-02T10:59Z  
4  https://android.googlesource.com/platform/exte...  2016-03-12T21:59Z

In [25]:
test_df.head()

Unnamed: 0   cwe_id                                             source  \
0           0  CWE-119  CWE-119 bool initiate_stratum ( struct pool * ...   
1           1  CWE-125  CWE-125 void eap_print ( netdissect_options * ...   
2           2  CWE-401  CWE-401 int ath9k_wmi_cmd ( struct wmi * wmi ,...   
3           3  CWE-399  CWE-399 static int yam_ioctl ( struct net_devi...   
4           4  CWE-189  CWE-189 static struct sk_buff * udp6_ufo_fragm...   

                                              target  \
0  <S2SV_ModStart> if ( ! valid_hex ( nonce1 ) <S...   
1  <S2SV_ModStart> case EAP_FRAME_TYPE_PACKET : N...   
2  <S2SV_ModStart> op_mutex ) ; kfree_skb ( skb )...   
3  <S2SV_ModStart> case SIOCYAMGCFG : memset ( & ...   
4  <S2SV_ModStart> ; if ( skb -> mac_header <S2SV...   

                               project_and_commit_id          cve_id  \
0  sgminer-dev@sgminer/e1c5050734123973b99d181c45...   CVE-2014-4502   
1  the-tcpdump-group@tcpdump/985122081165753c7442...  CVE-2017-13015   
2  torvalds@linux/728c1e2a05e4b5fc52fab3421dce772...  CVE-2019-19074   
3  torvalds@linux/8e3fbf870481eb53b2d3a322d1fc395...   CVE-2014-1446   
4  torvalds@linux/0e033e04c2678dbbe74a46b23fffb7b...   CVE-2013-4563   

                                    original_address               time  
0  https://github.com/sgminer-dev/sgminer/commit/...  2014-07-23T14:55Z  
1  https://github.com/the-tcpdump-group/tcpdump/c...  2017-09-14T06:29Z  
2  https://github.com/torvalds/linux/commit/728c1...  2019-11-18T06:15Z  
3  https://github.com/torvalds/linux/commit/8e3fb...  2014-01-18T22:55Z  
4  https://github.com/torvalds/linux/commit/0e033...  2013-11-20T13:19Z

In [26]:
train_df = train_df.drop(columns=['Unnamed: 0'])
test_df = test_df.drop(columns=['Unnamed: 0'])

num_train_rows = train_df.shape[0]
train_df['program_id'] = ['program_' + str(i) for i in range(1, num_train_rows + 1)]
last_program_id = train_df.shape[0]
test_df['program_id'] = ['program_' + str(i) for i in range(last_program_id + 1, last_program_id + 1 + test_df.shape[0])]

In [27]:
print(list(train_df.program_id.unique())[0])
print(list(train_df.program_id.unique())[-1])

print(list(test_df.program_id.unique())[0])
print(list(test_df.program_id.unique())[-1])

program_1
program_6776
program_6777
program_8482


In [28]:
test_source = set(test_df['source'])
train_source = set(train_df['source'])

common_source = test_source.intersection(train_source)

print(f"The number of common items between test_df and train_df is {len(common_source)}.")


The number of common items between test_df and train_df is 796.


In [29]:
for source in common_source:
    test_source = test_df[test_df['source'] == source]['source']
    train_source = train_df[train_df['source'] == source]['source']

    test_cve = test_df[test_df['source'] == source]['cve_id']
    train_cve = train_df[train_df['source'] == source]['cve_id']

    test_fix = test_df[test_df['source'] == source]['target']
    train_fix = train_df[train_df['source'] == source]['target']

    if not train_cve.unique() == test_cve.unique():
        print(f'test_df source: {test_source}')
        print(f'train_df source: {train_source}')
        print(f'train cve: {train_cve.unique()}, test_cve: {test_cve.unique()}')
        print(f'source equal: {test_source.unique() == train_source.unique()}')
        print(f'fix equal: {train_fix.unique() == test_fix.unique()}')
        print()

test_df source: 1038    CWE-119 static bool parse_reconnect ( struct p...
Name: source, dtype: object
train_df source: 3835    CWE-119 static bool parse_reconnect ( struct p...
Name: source, dtype: object
train cve: ['CVE-2014-4502'], test_cve: ['CVE-2014-4501']
source equal: [ True]
fix equal: [ True]

test_df source: 955    CWE-119 static void show_object ( struct objec...
Name: source, dtype: object
train_df source: 3446    CWE-119 static void show_object ( struct objec...
Name: source, dtype: object
train cve: ['CVE-2016-2315'], test_cve: ['CVE-2016-2324']
source equal: [ True]
fix equal: [ True]

test_df source: 897    CWE-119 static void finish_object ( struct obj...
Name: source, dtype: object
train_df source: 5499    CWE-119 static void finish_object ( struct obj...
Name: source, dtype: object
train cve: ['CVE-2016-2315'], test_cve: ['CVE-2016-2324']
source equal: [ True]
fix equal: [ True]

test_df source: 651    CWE-119 void traverse_commit_list ( struct rev...
Name: source, 

In [30]:
train_sources = set(train_df['source'])
test_sources = set(test_df['source'])

# Find the 'source' values that are only in test_sources
disjoint_sources = test_sources - train_sources

# Create disjoint_test by filtering test_df based on disjoint_sources
disjoint_test = test_df[test_df['source'].isin(disjoint_sources)]
print(f'Intersection: {test_df.shape[0] - disjoint_test.shape[0]}')

# Reset the index of the resulting DataFrame
disjoint_test = disjoint_test.drop_duplicates(subset=['source'])
disjoint_test = disjoint_test.reset_index(drop=True)
print(f'Disjoint Test Set Size: {disjoint_test.shape}')


Intersection: 798
Disjoint Test Set Size: (819, 8)


In [31]:
test_source = set(disjoint_test['source'])
train_source = set(train_df['source'])

common_source = test_source.intersection(train_source)

assert len(common_source) == 0

In [32]:
print(len(test_df.source.unique()), len(test_df.cve_id.unique()))
print(any(t_id in disjoint_test.cve_id.unique() for t_id in train_df.cve_id.unique()))

1615 943
True


In [33]:
import re

In [34]:
test_cve = set(disjoint_test['cve_id'])
train_cve = set(train_df['cve_id'])
common_cve = test_cve.intersection(train_cve)

for cve in common_cve:
    print(cve)
    train_source = train_df[train_df.cve_id == cve].reset_index(drop=True).source
    test_source = disjoint_test[disjoint_test.cve_id == cve].reset_index(drop=True).source

    pattern = r'CWE-\d+\s(.*)'
    train_matches = train_source.str.extract(pattern)
    test_matches = test_source.str.extract(pattern)

    train_set = set(train_matches[0])
    test_set = set(test_matches[0])

    disjoint_test = disjoint_test[~(disjoint_test['source'].str.extract(pattern)[0].isin(train_set))]
    filtered_source = disjoint_test[disjoint_test.cve_id == cve].reset_index(drop=True).source
    print(f'train: {train_source}')
    print(f'test: {test_source}')
    print(f'filtered: {filtered_source}')

    print('###')

CVE-2014-5353
train: 0    CWE-476 static krb5_error_code krb5_ldap_get_p...
Name: source, dtype: object
test: 0    CWE-000 static krb5_error_code krb5_ldap_get_p...
Name: source, dtype: object
filtered: Series([], Name: source, dtype: object)
###
CVE-2018-11506
train: 0    CWE-119 int sr_do_ioctl ( Scsi_CD * cd , struc...
Name: source, dtype: object
test: 0    CWE-787 int sr_do_ioctl ( Scsi_CD * cd , struc...
Name: source, dtype: object
filtered: Series([], Name: source, dtype: object)
###
CVE-2015-1870
train: 0    CWE-200 static unsigned create_oops_dump_dirs ...
1    CWE-200 static void ParseCommon ( map_string_t...
2    CWE-200 static int run_post_create ( const cha...
3    CWE-200 int main ( int argc , char * * argv ) ...
4    CWE-200 static void save_bt_to_dump_dir ( cons...
Name: source, dtype: object
test: 0    CWE-200 char * problem_data_save ( problem_dat...
1    CWE-200 static int create_problem_dir ( GHashT...
Name: source, dtype: object
filtered: 0    CWE-200 char * problem

In [35]:
disjoint_test.shape, test_df.shape

((692, 8), (1706, 8))

In [36]:
disjoint_test.head()

cwe_id                                             source  \
0  CWE-401  CWE-401 int ath9k_wmi_cmd ( struct wmi * wmi ,...   
1  CWE-189  CWE-189 static struct sk_buff * udp6_ufo_fragm...   
2  CWE-416  CWE-416 void CleanWriters ( GF_List * writers ...   
3  CWE-119  CWE-119 cJSON * cJSON_GetArrayItem ( cJSON * a...   
4  CWE-400  CWE-400 <S2SV_StartBug> void __perf_sw_event (...   

                                              target  \
0  <S2SV_ModStart> op_mutex ) ; kfree_skb ( skb )...   
1  <S2SV_ModStart> ; if ( skb -> mac_header <S2SV...   
2  <S2SV_ModStart> writers , 0 ) ; gf_list_del_it...   
3  <S2SV_ModStart> c = array ? array -> child : 0...   
4  <S2SV_ModStart> u64 nr , <S2SV_ModEnd> struct ...   

                               project_and_commit_id          cve_id  \
0  torvalds@linux/728c1e2a05e4b5fc52fab3421dce772...  CVE-2019-19074   
1  torvalds@linux/0e033e04c2678dbbe74a46b23fffb7b...   CVE-2013-4563   
2  gpac@gpac/5aba27604d957e960d8069d85ccaf868f8a7...  CVE-2020-35980   
3  esnet@iperf/91f2fa59e8ed80dfbf400add0164ee0e50...   CVE-2016-4303   
4  torvalds@linux/a8b0ca17b80e92faab46ee7179ba9e9...   CVE-2011-2918   

                                    original_address               time  \
0  https://github.com/torvalds/linux/commit/728c1...  2019-11-18T06:15Z   
1  https://github.com/torvalds/linux/commit/0e033...  2013-11-20T13:19Z   
2  https://github.com/gpac/gpac/commit/5aba27604d...  2021-04-21T16:15Z   
3  https://github.com/esnet/iperf/commit/91f2fa59...  2016-09-26T14:59Z   
4  https://github.com/torvalds/linux/commit/a8b0c...  2012-05-24T23:55Z   

     program_id  
0  program_6779  
1  program_6781  
2  program_6784  
3  program_6787  
4  program_6790

In [37]:
train_df.head()

cwe_id                                             source  \
0  CWE-000  CWE-000 static void unix_release_sock ( struct...   
1  CWE-200  CWE-200 static void snd_timer_user_tinterrupt ...   
2  CWE-119  CWE-119 static void store_coding_context ( MAC...   
3  CWE-000  CWE-000 static int ext4_write_begin ( struct f...   
4  CWE-119  CWE-119 <S2SV_StartBug> int16_t vp9_ac_quant (...   

                                              target  \
0  <S2SV_ModStart> ) ; } unix_dgram_peer_wake_dis...   
1  <S2SV_ModStart> resolution ) { memset ( & r1 ,...   
2  <S2SV_ModStart> int mode_index , <S2SV_ModEnd>...   
3  <S2SV_ModStart> = page ; if ( ext4_should_dior...   
4  <S2SV_ModStart> , int delta , vpx_bit_depth_t ...   

                               project_and_commit_id         cve_id  \
0  torvalds@linux/7d267278a9ece963d77eefec6163022...  CVE-2013-7446   
1  torvalds@linux/e4ec8cc8039a7063e24204299b462bd...  CVE-2016-4578   
2  external@libvpx/5a9753fca56f0eeb9f61e342b2fccf...  CVE-2016-1621   
3  torvalds@linux/744692dc059845b2a3022119871846e...  CVE-2015-8324   
4  external@libvpx/5a9753fca56f0eeb9f61e342b2fccf...  CVE-2016-1621   

                                    original_address               time  \
0  https://github.com/torvalds/linux/commit/7d267...  2015-12-28T11:59Z   
1  https://github.com/torvalds/linux/commit/e4ec8...  2016-05-23T10:59Z   
2  https://android.googlesource.com/platform/exte...  2016-03-12T21:59Z   
3  https://github.com/torvalds/linux/commit/74469...  2016-05-02T10:59Z   
4  https://android.googlesource.com/platform/exte...  2016-03-12T21:59Z   

  program_id  
0  program_1  
1  program_2  
2  program_3  
3  program_4  
4  program_5

In [38]:
test_df.head()

cwe_id                                             source  \
0  CWE-119  CWE-119 bool initiate_stratum ( struct pool * ...   
1  CWE-125  CWE-125 void eap_print ( netdissect_options * ...   
2  CWE-401  CWE-401 int ath9k_wmi_cmd ( struct wmi * wmi ,...   
3  CWE-399  CWE-399 static int yam_ioctl ( struct net_devi...   
4  CWE-189  CWE-189 static struct sk_buff * udp6_ufo_fragm...   

                                              target  \
0  <S2SV_ModStart> if ( ! valid_hex ( nonce1 ) <S...   
1  <S2SV_ModStart> case EAP_FRAME_TYPE_PACKET : N...   
2  <S2SV_ModStart> op_mutex ) ; kfree_skb ( skb )...   
3  <S2SV_ModStart> case SIOCYAMGCFG : memset ( & ...   
4  <S2SV_ModStart> ; if ( skb -> mac_header <S2SV...   

                               project_and_commit_id          cve_id  \
0  sgminer-dev@sgminer/e1c5050734123973b99d181c45...   CVE-2014-4502   
1  the-tcpdump-group@tcpdump/985122081165753c7442...  CVE-2017-13015   
2  torvalds@linux/728c1e2a05e4b5fc52fab3421dce772...  CVE-2019-19074   
3  torvalds@linux/8e3fbf870481eb53b2d3a322d1fc395...   CVE-2014-1446   
4  torvalds@linux/0e033e04c2678dbbe74a46b23fffb7b...   CVE-2013-4563   

                                    original_address               time  \
0  https://github.com/sgminer-dev/sgminer/commit/...  2014-07-23T14:55Z   
1  https://github.com/the-tcpdump-group/tcpdump/c...  2017-09-14T06:29Z   
2  https://github.com/torvalds/linux/commit/728c1...  2019-11-18T06:15Z   
3  https://github.com/torvalds/linux/commit/8e3fb...  2014-01-18T22:55Z   
4  https://github.com/torvalds/linux/commit/0e033...  2013-11-20T13:19Z   

     program_id  
0  program_6777  
1  program_6778  
2  program_6779  
3  program_6780  
4  program_6781

In [39]:
train_df = train_df.drop_duplicates(subset='source', keep='first')
test_df = test_df.drop_duplicates(subset='source', keep='first')

In [40]:
unique_targets = train_df['target'].unique()

for target_value in unique_targets:
    sources_for_target = train_df[train_df['target'] == target_value]['source'].unique()

    if len(sources_for_target) != 1:
        print(f"Target: {target_value}")
        print("Sources:")
        for idx, source_value in enumerate(sources_for_target):
            print(f'{idx}: {source_value}')
        print()

Target: <S2SV_ModStart> Rec . RecordLength ) ; if ( Rec . RecordLength > GetBlobSize ( image ) ) ThrowReaderException ( CorruptImageError , "ImproperImageHeader"

Sources:
0: CWE-400 static Image * ReadWPGImage ( const ImageInfo * image_info , ExceptionInfo * exception ) { typedef struct { size_t FileId ; MagickOffsetType DataOffset ; unsigned int ProductType ; unsigned int FileType ; unsigned char MajorVersion ; unsigned char MinorVersion ; unsigned int EncryptKey ; unsigned int Reserved ; } WPGHeader ; typedef struct { unsigned char RecType ; size_t RecordLength ; } WPGRecord ; typedef struct { unsigned char Class ; unsigned char RecType ; size_t Extension ; size_t RecordLength ; } WPG2Record ; typedef struct { unsigned HorizontalUnits ; unsigned VerticalUnits ; unsigned char PosSizePrecision ; } WPG2Start ; typedef struct { unsigned int Width ; unsigned int Height ; unsigned int Depth ; unsigned int HorzRes ; unsigned int VertRes ; } WPGBitmapType1 ; typedef struct { unsigned int Wi

Target: <S2SV_ModStart> 0.0 ) ; ( void ) CloneString ( & <S2SV_ModStart> draw_info -> geometry , <S2SV_ModEnd> geometry ) ;

Sources:
0: CWE-399 static Image * ReadCAPTIONImage ( const ImageInfo * image_info , ExceptionInfo * exception ) { char * caption , geometry [ MaxTextExtent ] , * property , * text ; const char * gravity , * option ; DrawInfo * draw_info ; Image * image ; MagickBooleanType split , status ; register ssize_t i ; size_t height , width ; TypeMetric metrics ; assert ( image_info != ( const ImageInfo * ) NULL ) ; assert ( image_info -> signature == MagickSignature ) ; if ( image_info -> debug != MagickFalse ) ( void ) LogMagickEvent ( TraceEvent , GetMagickModule ( ) , "%s" , image_info -> filename ) ; assert ( exception != ( ExceptionInfo * ) NULL ) ; assert ( exception -> signature == MagickSignature ) ; image = AcquireImage ( image_info ) ; ( void ) ResetImagePage ( image , "0x0+0+0" ) ; option = GetImageOption ( image_info , "filename" ) ; if ( option == ( const ch

In [41]:
unique_targets = disjoint_test['target'].unique()

for target_value in unique_targets:
    sources_for_target = disjoint_test[disjoint_test['target'] == target_value]['source'].unique()

    if len(sources_for_target) != 1:
        print(f"Target: {target_value}")
        print("Sources:")
        for idx, source_value in enumerate(sources_for_target):
            print(f'{idx}: {source_value}')
        print()

Target: <S2SV_ModStart> . left ; luaL_checkstack ( L , 1 , "in<S2SV_blank>function<S2SV_blank>mp_unpack_full" ) ;

Sources:
0: CWE-787 int mp_unpack_full ( lua_State * L , int limit , int offset ) { size_t len ; const char * s ; mp_cur c ; int cnt ; int decode_all = ( ! limit && ! offset ) ; s = luaL_checklstring ( L , 1 , & len ) ; if ( offset < 0 || limit < 0 ) return luaL_error ( L , "Invalid<S2SV_blank>request<S2SV_blank>to<S2SV_blank>unpack<S2SV_blank>with<S2SV_blank>offset<S2SV_blank>of<S2SV_blank>%d<S2SV_blank>and<S2SV_blank>limit<S2SV_blank>of<S2SV_blank>%d." , offset , len ) ; else if ( offset > len ) return luaL_error ( L , "Start<S2SV_blank>offset<S2SV_blank>%d<S2SV_blank>greater<S2SV_blank>than<S2SV_blank>input<S2SV_blank>length<S2SV_blank>%d." , offset , len ) ; if ( decode_all ) limit = INT_MAX ; mp_cur_init ( & c , ( const unsigned char * ) s + offset , len - offset ) ; for ( cnt = 0 ; c . left > 0 && cnt < limit ; cnt ++ ) { mp_decode_to_lua_type ( L , & c ) ; if ( c . 

In [42]:
print(sum([elem.strip() == '' for elem in train_df['target']]))
print(sum([elem.strip() == '' for elem in disjoint_test['target']]))
print(sum([elem.strip() == '' for elem in test_df['target']]))


25
5
9


In [43]:
train_df = train_df[train_df['target'].str.strip() != '']
disjoint_test = disjoint_test[disjoint_test['target'].str.strip() != '']
test_df = test_df[test_df['target'].str.strip() != '']

In [44]:
print(sum([elem.strip() == '' for elem in train_df['target']]))
print(sum([elem.strip() == '' for elem in disjoint_test['target']]))
print(sum([elem.strip() == '' for elem in test_df['target']]))

0
0
0


In [45]:
train_df.to_csv('train.csv')
disjoint_test.to_csv('cleantest.csv')
test_df.to_csv('test.csv')

In [46]:
data = load_dataset("nus-yam/bigfixes", streaming=True)

train_data = data['train'].take(None)
test_data = data['test'].take(None)
clean_test = data['cleantest'].take(None)

In [47]:
print(len(list(train_data)), len(list(test_data)), len(list(clean_test)))

5158 1606 687


In [48]:
test_df.shape, disjoint_test.shape

((1606, 8), (687, 8))

In [49]:
print(list(train_df.program_id.unique())[0])
print(list(train_df.program_id.unique())[-1])

print(list(test_df.program_id.unique())[0])
print(list(test_df.program_id.unique())[-1])

print(list(disjoint_test.program_id.unique())[0])
print(list(disjoint_test.program_id.unique())[-1])

program_1
program_6776
program_6777
program_8479
program_6779
program_8479


In [50]:
any(program_id in test_df.program_id.unique() for program_id in train_df.program_id.unique())

False

In [51]:
any(program_id in disjoint_test.program_id.unique() for program_id in train_df.program_id.unique())

False

In [52]:
any(program_id in disjoint_test.program_id.unique() for program_id in test_df.program_id.unique())

True